<img src="./images/DLI_Header.png" width=400/>

# Fundamentals of Accelerated Data Science # 

In [1]:
# DO NOT CHANGE THIS CELL
import cudf
import cuml

import cuxfilter as cxf

In [2]:
# DO NOT CHANGE THIS CELL
gdf = cudf.read_csv('./data/clean_uk_pop.csv', usecols=['easting', 'northing'])
print(gdf.dtypes)
gdf.shape

northing    float64
easting     float64
dtype: object


(58479894, 2)

In [3]:
gdf.head()

northing      easting
0  515491.5313  430772.1875
1  503572.4688  434685.8750
2  517903.6563  432565.5313
3  517059.9063  427660.6250
4  509228.6875  425527.7813

In [4]:
# DO NOT CHANGE THIS CELL
# instantaite
km = cuml.KMeans(n_clusters=5)

# fit
km.fit(gdf)

# assign cluster as new column
gdf['cluster'] = km.labels_
km.cluster_centers_

0              1
0  306647.898235  408370.452191
1  442109.465392  402673.747673
2  288997.149971  553805.430444
3  148770.463641  311786.805381
4  170553.110214  521605.459724

In [5]:
gdf

northing      easting  cluster
0         515491.5313  430772.1875        1
1         503572.4688  434685.8750        1
2         517903.6563  432565.5313        1
3         517059.9063  427660.6250        1
4         509228.6875  425527.7813        1
...               ...          ...      ...
58479889  192393.7813  340519.8438        3
58479890  183451.8906  337749.6250        3
58479891  189997.5156  341165.1250        3
58479892  184439.1250  335227.6563        3
58479893  187036.3281  342634.5313        3

[58479894 rows x 3 columns]

In [ ]:
from pyproj import CRS
import numpy as np
from pyproj import Transformer

crs_UK = CRS.from_epsg(27700) # GB coord system
crs_world = CRS.from_epsg(3857) # used by maps WGS 84

transformed = Transformer.from_crs(crs_UK, crs_world).transform(gdf["easting"].to_numpy(), gdf["northing"].to_numpy())

In [19]:
tdf = cudf.DataFrame(np.column_stack(transformed), columns=["easting", "northing"])
tdf["cluster"] = gdf["cluster"]

In [21]:
ncolors = gdf["cluster"].nunique()
ncolors

5

In [22]:
from bokeh.palettes import Category10 # 10 will be enough

In [ ]:
cxf_data = cxf.DataFrame.from_dataframe(tdf)

In [ ]:
scatter_chart = cxf.charts.datashader.scatter(
    x='easting', y='northing', 
    aggregate_col="cluster",
    aggregate_fn="mean",
    tile_provider="CartoDark",
    legend=False,
    color_palette=Category10[ncolors],
    unselected_alpha=0,
)
cluster_widget = cxf.charts.panel_widgets.multi_select('cluster')


In [87]:
dash = cxf_data.dashboard(charts=[scatter_chart],sidebar=[cluster_widget], theme=cxf.themes.dark, data_size_widget=True)

In [88]:
dash.app()

GridSpec(ncols=12, nrows=5)
    [0] GridSpec(height=800, ncols=12, nrows=5, sizing_mode='fixed', width=1200)
        [0] HoloViews(DynamicMap, height=800, sizing_mode='stretch_both', width=1200)
    [1] WidgetBox(styles={'border-color': '...})
        [0] Number(css_classes=['indicator'], default_color='#2B2B2B', font_size='18pt', format='{value:,}', name='Datapoints Selected', sizing_mode='stretch_width', title_size='14pt', value=58479894)
        [1] Progress(sizing_mode='stretch_width', styles={'--success-bg-color': '...}, value=100)
    [2] Column(min_height=500, sizing_mode='stretch_width')
        [0] MultiChoice(name='cluster', options=[1, 0, 2, 4, 3], sizing_mode='scale_width', styles={'color': '#2B2B2B'}, stylesheets=['\n                .choic...])

In [89]:
dash.app()

GridSpec(ncols=12, nrows=5)
    [0] GridSpec(height=800, ncols=12, nrows=5, sizing_mode='fixed', width=1200)
        [0] HoloViews(DynamicMap, height=800, sizing_mode='stretch_both', width=1200)
    [1] WidgetBox(styles={'border-color': '...})
        [0] Number(css_classes=['indicator'], default_color='#2B2B2B', font_size='18pt', format='{value:,}', name='Datapoints Selected', sizing_mode='stretch_width', title_size='14pt', value=58479894)
        [1] Progress(sizing_mode='stretch_width', styles={'--success-bg-color': '...}, value=100)
    [2] Column(min_height=500, sizing_mode='stretch_width')
        [0] MultiChoice(name='cluster', options=[1, 0, 2, 4, 3], sizing_mode='scale_width', styles={'color': '#2B2B2B'}, stylesheets=['\n                .choic...])

In [43]:
dash.stop()

In [41]:
dash.show("http://34.204.188.189/", port=8789)

Dashboard running at port 8789


Row
    [0] Button(button_type='success', name='open cuxfilter d...)

Task exception was never retrieved
future: <Task finished name='Task-427401' coro=<WebSocketProtocol13.write_message.<locals>.wrapper() done, defined at /opt/conda/lib/python3.10/site-packages/tornado/websocket.py:1086> exception=WebSocketClosedError()>
Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/tornado/websocket.py", line 1088, in wrapper
    await fut
tornado.iostream.StreamClosedError: Stream is closed

During handling of the above exception, another exception occurred:

Traceback (most recent call last):
  File "/opt/conda/lib/python3.10/site-packages/tornado/websocket.py", line 1090, in wrapper
    raise WebSocketClosedError()
tornado.websocket.WebSocketClosedError


In [36]:
import IPython
app = IPython.Application.instance()
app.kernel.do_shutdown(True)

{'status': 'ok', 'restart': True}

**Well Done!** Let's move to the [next notebook](3-03_dbscan.ipynb). 

<img src="./images/DLI_Header.png" width=400/>